<div style="width:75%;margin:0 auto;text-align:center;">

<h1>
Graph project: Epidemic spreading <br/>
ENSEEIHT SN <br/>
</h1>

<h3>
FAINSIN Laurent <br/>
GUILLOTIN Damien
</h3>

<div style="width:75%;margin:0 auto;text-align:justify;">
    
## Introduction
    
As you know, a new epidemic has overwhelmed the world, COVID-19 jeopardizes people and changes our habits. It is easy to realise that knowing how illnesses spread is vital to our own protection. How can we predict whether a disease will cause an epidemic, how many people it will infect, which people it will infect, and whether or not it is dangerous to society as a whole ? Also, how can we determine which techniques to use in fighting an epidemic once it begins ? One way to answer all of these questions is through **mathematical modeling**.

In this work you will have to review different epidemic modelings relying all on the representation by graphs of a human network called a **contact network**. A vertex in a contact network represents an individual and an edge between two vertices represents a contact between two individuals. The disease only spread from individual to individual if they are in contact, so through the edges. This representation is actually really common in research, and a lot of state-of-the-art modeling are built over it. From these different models you will be asked to draw conclusions from experiments on varying contact networks.

For readability and ease of use, this project will be carried on a Jupyter Notebook, hence code and question answering have to be written in this unique file. This is a **DUO** project, no group of one person will be accepted, the duo has to be composed of same TD group students, if the number of students in the TD group is odd we will accept one group composed of three students. It will be coded in Julia using the LightGraphs package. **BEWARE:** 
    
- If the code does not provide good results, its readability as well as its comments are essential for the corrector to potentially find some notation points.
- The specifications of the functions have to be strictly respected.
- Do not neglect written questions they stand for an important part of the notation, you are not only evaluated on the coding. Also, even so a written question may not ask you directly to code or provide results from code, support your arguments when possible with a runable example is very welcome and sometimes even expected.
- Any initiatives and additional efforts bringing contents and thoughts out of the question scope may result in bonus points if pertinent.

Deliverable: You will deliver your work on moodle before **23.01.2022** in a **.tar** containing the notebook with your codes and your written answers, and the different graph figures in .png you will generate. The corrector will use the student N7 computers for running your code, so take care of verifying that your work is running as expected on these computers !

LightGraphs documentation: <https://juliagraphs.org/LightGraphs.jl/v1.2/index.html>

<div style="width:75%;margin:0 auto;text-align:justify;">

## Environment and packages installation

**mathematical modeling**: For evaluation, coding questions have to run with no additional packages ! Only the ones present here ! However if you want to use another package to go further in your answer and add bonus contents, take care of separating the cells and precising which packages you are using.

In [ ]:
# TO RUN ONCE
using Pkg
Pkg.activate(".") # Path to Manifest.toml and Project.toml
Pkg.resolve()

In [ ]:
# Import packages
using Pkg
Pkg.activate(".") # Path to Manifest.toml and Project.toml

using Graphs
using Graphs: smallgraph
using Graphs: stochastic_block_model
using Graphs: barabasi_albert
using Graphs: random_regular_graph
using GraphPlot

using Colors
using CairoMakie
using StatsBase
using Plots
using JLD2
using Compose
using Random

<div style="width:75%;margin:0 auto;text-align:justify;">

## Part 1 - SIS model

SIS is a compartmental model, ie a model where the population is divided into subgroups that represent the disease status of its members. SIS stands for Susceptible $\rightarrow$ Infected $\rightarrow$ Susceptible where the susceptible group contains those who remain susceptible to the infection, and the infected group consists of those who not only have the disease but are also in the contagious period of the disease.


Combine with a contact network approach, this model can capture contact patterns (family, company, friends). Each vertex represents an individual in the host population, and contacts between two individuals are represented by an edge that connects the two. The probability of transmitting the disease from an infected to a susceptible individual along one of these edges or contacts is $\beta$ (=**mathematical modeling**).

In order for a disease to begin spreading through a network, the disease must be introduced into the population, either through infecting a proportion of the population or through infecting one individual. As time moves forward, the disease will spread away from those initially infected, and two things may occur simultaneously at each time step $t$. First, each infected individual will spread disease to each of its contacts with a probability $\beta$. Secondly, each infectious individual will recover at a rate, $\alpha$, at which point the individual will then no longer infect any of its contacts. After the disease has run its course, we can determine how the disease affected the network by calculating various quantities that help us better understand the outbreak.

###### P. Van Mieghem, J. Omic, R. E. Kooij, _“Virus Spread in Networks”_, IEEE/ACM Transaction on Networking (2009)

<div style="width:75%;margin:0 auto;text-align:justify;">

### 1.1 Contact networks sample

In [ ]:
# Susceptible, Infected, Recovered, Alerted
node_colors = [colorant"lightseagreen", colorant"orange", colorant"purple", colorant"red"]

In [ ]:
# karat7: A graph representing the karate club of N7 and the connections between the persons in this club. There are 34 people in this network. It is actually inspired by one of the most famous problem in graph theory: the Zachary's karate club.

karat7 = smallgraph(:karate)
nodecolor = [node_colors[1]]
plot = gplot(karat7, nodefillc = nodecolor)
draw(PNG("img/q0_1.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# n7_2A: A graph representing the second year students at N7. Each department (SN, MF2E, 3EA) form a community where connections are denser, connections between department are rarer.

n = [100, 70, 50]
c = [[10, 0, 0] [0.1, 10, 0] [0.1, 0.1, 10]]
n7_2A = stochastic_block_model(c, n)
nodecolor = [node_colors[1]]
plot = gplot(n7_2A, nodefillc = nodecolor)
draw(PNG("img/q0_2.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# toulouse_neigh: A graph representing a neighborhood composed of 1000 people in Toulouse.

toulouse_neigh = barabasi_albert(1000, 1)
nodecolor = [node_colors[1]]
plot = gplot(toulouse_neigh, nodefillc = nodecolor)
draw(PNG("img/q0_3.png", 100cm, 100cm), plot)
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">
  
### 1.2 Introduce the infection
    
We denote by `state` a vector containing the disease status of each vertex where Susceptible=0 and Infected=1. Then `state` is an `Array{Int32,1}` of length the number of vertices. This array in addition of a graph (represented internally by an adjacency matrix or an adjacency list) will be the data structure of our model.
    
In `Array{Int32,1}`, `Int32` refers to the kind of data in the array, here 32 bits integers, `1` refers to the dimension of the array, here we have a 1-dimensional structure so a vector

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cornflowerblue">Question 1 (code):</strong> For each graph in the graph sample (`state`, `n7_2A`, `toulouse_neigh`) initialize the state array by assigning each vertex to susceptible and add randomly one or numerous infected people. Save the graph as a .png image using `state` and `Int32`, infected should appear in a different color (`colorant"orange"`).
    
Due to a bug on certain version of Jupyter Notebook, the graph figures should be saved in a file and not plot inside the notebook !!!
    
Gplot GitHub: <https://github.com/JuliaGraphs/GraphPlot.jl>
    
Gplot examples: <https://juliagraphs.org/GraphPlot.jl/>

In [ ]:
function new_state(net, ni)
    return shuffle(vcat(
        ones(Int, ni),
        zeros(Int, nv(net) - ni)
    ))
end

In [ ]:
# Infect Karat7
karat7_state = new_state(karat7, 5)
nodefillc = node_colors[karat7_state.+1]
plot = gplot(karat7, nodefillc = nodefillc)
draw(PNG("img/q1_1.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Infect n7_2A
n7_2A_state = new_state(n7_2A, 10)
nodefillc = node_colors[n7_2A_state.+1]
plot = gplot(n7_2A, nodefillc = nodefillc)
draw(PNG("img/q1_2.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Infect Toulouse_neigh
toulouse_neigh_state = new_state(toulouse_neigh, 50)
nodefillc = node_colors[toulouse_neigh_state.+1]
plot = gplot(toulouse_neigh, nodefillc = nodefillc)
draw(PNG("img/q1_3.png", 100cm, 100cm), plot)
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cornflowerblue">Question 2 (written):</strong> What do you think/predict about the influence of the initial number of infected people and their locations on the evolution of an SIS model epidemic ?

> Plus le nombre initial d'infectés sera élevé, et plus l'épidémie va se propager rapidement. De plus, plus la répartition initial des infectés dans la population est uniforme, plus la propagation de l'épidemie sera rapide.

<div style="width:75%;margin:0 auto;text-align:justify;">
  
### 1.3 Spread the infection

<div style="width:75%;margin:0 auto;text-align:justify;">
      
<strong style="color:cornflowerblue">Question 3 (code):</strong> Implement the function `SIS` (respect the header and the specifications). You can use `state` to translate the probabilities. Test your algorithm on `karat7`, `n7_2A`, and `toulouse_neigh` with arbitrary $\beta$, $\alpha$, and $t$.
    
###### The corrector should be able to write `new_state = SIS(net,state,beta,alpha,t)` with your code.

In [ ]:
"""
Take a contact network at a certain state and apply t time steps of an SIS model.

* PARAMS
    - net (LightGraph): graph representing the contact network
    - state (Array{Int32,1}): disease status of each vertex
    - beta (Float64): infection rate
    - alpha (Float64): curing rate
    - time (Int32): number of time step

* RETURNS
    - (Array{Int32,1}): the new state of the contact network after t time steps
"""
function SIS(net, state, beta, alpha, time)
    X = zeros(time+1, 2)
    adjacent_matrix = adjacency_matrix(net)
    n = nv(net)

    X[1, 1] = sum(state .== 0)
    X[1, 2] = sum(state .== 1)

    for t = 2:(time+1)
        # println("-"^50, t)
        # println("state_0  = ", state)

        # on trouve le nombre de voisins de chaque individus
        adjacent_infected = adjacent_matrix * (state .== 1)
        # println("adjacent = ", number_infected_adjacent)

        # calcul des probas d'infection
        proba_infection = (state .== 0) .* (adjacent_infected .!= 0) .* (1 .- (
            (state .== 0) .* fill(1 - beta, n)
        ) .^ adjacent_infected)
        # println("proba_i  = ", proba_infection

        # tirage au sort des infections
        state[((state.==0).*(adjacent_infected.!=0).*rand(n)).<proba_infection] .= 1
        # println("state_i  = ", state)

        # tirage au sort des guérisons
        state[((state.==1).*rand(n)).>(1-alpha)] .= 0
        # println("state_g  = ", state)

        X[t, 1] = sum(state .== 0)
        X[t, 2] = sum(state .== 1)
    end
    return state, X
end

In [ ]:
# Test on karat7
karat7_state = new_state(karat7, 5)
state, X = SIS(karat7, karat7_state, 0.9, 0.3, 10)

plot = Plots.plot(1:size(X)[1], X, labels=["Susceptible" "Infected"], palette=node_colors)
png("img/q3_1p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(karat7, nodefillc = nodefillc)
draw(PNG("img/q3_1g.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Test on N7_2A
n7_2A_state = new_state(n7_2A, 10)
state, X = SIS(n7_2A, n7_2A_state, 0.5, 0.3, 10)

plot = Plots.plot(1:size(X)[1], X,labels=["Susceptible" "Infected"], palette=node_colors)
png("img/q3_2p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(n7_2A, nodefillc = nodefillc)
draw(PNG("img/q3_2g.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Test on Toulouse_neigh
toulouse_neigh_state = new_state(toulouse_neigh, 50)
state, X = SIS(toulouse_neigh, toulouse_neigh_state, 0.8, 0.2, 100)

plot = Plots.plot(1:size(X)[1], X, labels=["Susceptible" "Infected"], palette=node_colors)
png("img/q3_3p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(toulouse_neigh, nodefillc = nodefillc)
draw(PNG("img/q3_3g.png", 100cm, 100cm), plot)
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

### 1.4 Simulate and understand the epidemic
    
In the SIS model of this project, every disease is characterized by:

* The infection rate $\beta$ representing the chance of infection when being in contact with an infected individual.
* The curing rate $\alpha$ representing the chance of being cured of the disease.
* The effective spreading rate $\tau=\frac{\beta}{\alpha}$ representing the capacity of the disease to spread. More the disease infect easily ($\beta$ high) and less it is cured easily ($\alpha$ low) more $\tau$ can be high.

We are now willing to understand what are the influences of these parameters as well as the contact network shape on an epidemic.

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 4 (written):</strong> The function `SIS` you implemented launches one run of an SIS model on a given contact network. As it makes use of randomness, one run of spreading is stochastic. Then what simple method can you propose to provide a prediction of the disease spreading on a given contact network ?

> Pour obtenir une prédiction d'un modèle SIS, on peut simplement executer la simulation un grand nombre de fois et ensuite tracer la moyenne de ces simulations.

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 5 (code):</strong> Implement the function `Simulation_SIS` (respect the header and the specifications).
    
###### The corrector should be able to write `predictions, taus = Simulation_SIS(net,nbinf,betas,alphas,t,nbsimu)` with your code.

In [ ]:
"""
Take a contact network, different diseases (defined by  different parameters alpha and beta), a number of initial infected people and process nbsimu simulations of SIS over t time steps. You will provide the prediction of the  percentage of infected at each time t as well as the  spreading rate of each disease.

* PARAMS
    - net (LightGraph): graph representing the contact network
    - nbinf (Int32): number of infected at the start of each simulation
    - betas (Array{Float64,1}): array of infection rate on edges
    - alphas (Array{Float64,1}): array of curing rate on vertices
    - time (Int32): number of time step
    - nbsimu (Int32): number of simulations

* RETURNS
    - (Array{Float64,2}): the prediction of the percentage of infected at each time step and for each disease. The first dimension contains the time steps and the second contains the diseases
    - (Array{Float64,1}): effective spreading rate for each disease
"""
function Simulation_SIS(net, nbinf, betas, alphas, t, nbsimu)
    taus = zeros(length(alphas))
    prediction = zeros(t+1, length(taus))

    for (i, (beta, alpha)) in enumerate(zip(betas, alphas))
        taus[i] = round(beta / alpha, digits = 2)
        for _ in 1:nbsimu
            state = new_state(net, nbinf)
            _, X = SIS(net, state, beta, alpha, t)
            prediction[:, i] += X[:, 2] ./ nbsimu ./ length(state)
        end
    end

    return prediction, taus
end

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 6 (written)</strong>: Run the 2 scripts below and describe what you see. Conclude on the influence of $\tau$, $\beta$, and $\alpha$ on an epidemic we can model with SIS.
    
> Il semblerait que plus $\tau$ est élevé, plus le pourcentage d'infectés augmente rapidement en fonction du temps.

In [ ]:
# Script launching predictions on different diseases on karat7 and printing the precentage of infected at each time step.
betas = [0.05, 0.1, 0.01, 0.4, 0.04, 0.05, 0.005]
alphas = [0.05, 0.1, 0.01, 0.1, 0.01, 0.1, 0.01]

predictions, taus = Simulation_SIS(karat7, 2, betas, alphas, 100, 1000)
plot = Plots.plot(predictions, label = taus', xlabel = "Time", ylabel = "% of infected")
png("img/q6_1.png")
display(plot)

In [ ]:
# Same as before but applied on n7_2A.
betas = [0.05, 0.1, 0.01, 0.4, 0.04, 0.05, 0.005]
alphas = [0.05, 0.1, 0.01, 0.1, 0.01, 0.1, 0.01]

predictions, taus = Simulation_SIS(n7_2A, 100, betas, alphas, 100, 100)
plot = Plots.plot(predictions, label = taus', xlabel = "Time", ylabel = "% of infected")
png("img/q6_2.png")
display(plot)

In [ ]:
# Same as before but applied on toulouse_neigh. May be a bit long to run.
betas = [0.05, 0.1, 0.15, 0.25, 0.35, 0.45, 0.55, 0.65, 0.75, 0.85, 0.95]
alphas = [0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2]

predictions, taus = Simulation_SIS(toulouse_neigh, 100, betas, alphas, 100, 100)
plot = Plots.plot(predictions, label = taus', xlabel = "Time", ylabel = "% of infected")
png("img/q6_3.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 7 (written):</strong> Change the initial number of infected in the scripts above, is it in accordance with your answer in Question 2 ?

> On remarque que plus l'on augmente le nombre initial d'infecté, plus le pourcentage d'infectés dans la population converge rapidement.

In [ ]:
# Change the initial number of infected
betas = [0.5]
alphas = [0.2]

plot = Plots.plot()
for i in [5 10 50 100]
    predictions, _ = Simulation_SIS(toulouse_neigh, i, betas, alphas, 50, 100)
    Plots.plot!(predictions, label = i, xlabel = "Time", ylabel = "% of infected")
end

png("img/q7.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cornflowerblue">Question 8 (code):</strong> Implement a script plotting the maximum percentage of infected people according to $\tau$ over 300 time steps for 3 contact networks:

* A regular graph of 200 vertices with degree 2.
* A regular graph of 200 vertices with degree 5.
* A regular graph of 200 vertices with degree 10.

You can use the function `random_regular_graph(n,d)` of LighGraphs. As you probably need to use a certain number of different values of $\tau$ to visualize something interesting (the more there are the more the figure will be smooth) you should fix $\alpha$ and make $\beta$ vary. 

###### A regular graph is a graph where each vertex has the same degree.

In [ ]:
display(gplot(random_regular_graph(200, 2)))
display(gplot(random_regular_graph(200, 5)))
display(gplot(random_regular_graph(200, 10)))

In [ ]:
# Plots of the maximum percentage of infected people according to tau over 300 time steps for 3 contact networks.
n = 200
betas = 0.01:0.01:0.99
alphas = fill(0.15, length(betas))

plot = Plots.plot()
for d in [2 3 4 5 10]
    net = random_regular_graph(n, d)
    predictions, taus = Simulation_SIS(net, 5, betas, alphas, 300, 100)
    max_infected = [maximum(col) for col in eachcol(predictions)]
    Plots.plot!(max_infected, label = d, xlabel = "τ", ylabel = "% of infected")
end

png("img/q8.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 9 (written):</strong> Describe the figure and draw conclusions on the epidemic behavior for different degrees $d$ on regular graphs. Thus, in addition of the inner properties of the disease ($\alpha$, $\beta$, $\tau$) what other parameter is essential in the spreading ? Finally, what analogy can be done with real life from this experiment ?
    
> Le degré $d$ du graphe représente le nombre de connections par individus. Ainsi plus $d$ est elevé plus individus se connaissent entre eux et plus l'infection est rapide. On l'observe sur le graphique, le taux d'infectés est directement proportionnel à $d$.

<div style="width:75%;margin:0 auto;text-align:justify;">

## Part 2 - SIR and SAIR model
    
Unfortunately SIS model is valuable for diseases we can catch back since a cured person can get ill again. This is true for the flu, the cold, etc. However COVID-19 might create immunity for whom already got it and SIS can not take into account immune or dead persons. That is why we propose in this part to consider another model more adapted to COVID-19 called SIR. It stands for Susceptible $\rightarrow$ Infected $\rightarrow$ Recovered where the susceptible group contains those who remain susceptible to the infection, the infected group consists of those who not only have the disease but are also in the contagious period of the disease, and the recovered group contains those who were ill, got cured, are not contagious and can not get ill anymore.

###### M. Youssef and C. Scoglio, _"An individual-based approach to SIR epidemics in contact networks"_, Journal of Theoretical Biology 283 (2011)
    
One limitation of SIR is that it does not model the reaction of humans when they feel the presence of the epidemic. Indeed, if feeling threaten or surrounded by infected, an individual may change its behaviors: wear mask, wash its hands, etc. This result in a smaller infection rate. That is why in this part we will also consider a variant of SIR called SAIR which stands for Susceptible $\rightarrow$ Alert $\rightarrow$ Infected $\rightarrow$ Recovered. A susceptible individual becomes infected by the infection rate $\beta_0$, an infected individual recovers and gets immune by the curing rate $\alpha$, an individual can observe the states of its neighbors, then a susceptible individual might go to the alert state if surrounded by infected individuals with an alert rate $\kappa$ on each contact with an infected, an alert inividual becomes infected by the infection rate $\beta_1$ where $0<\beta_1<\beta_0$. In our simple SAIR model, an individual can not go back to a susceptible state when he got into the alert state.

###### F. Darabi Sahneh and C. Scoglio, _"Epidemic Spread in Human Networks"_, 50th IEEE Conf. Decision and Contol, Orlando, Florida (2011)

<div style="width:75%;margin:0 auto;text-align:justify;">

### 2.1 SIR
    
The vector containing the disease status `state` has to change a bit since we added a new state. Hence it will be an `Array{Int32,1}` where Susceptible=0, Infected=1, and Recovered=2.

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 10 (code):</strong> Implement the function `SIR` (respect the header and the specifications). You can use `state` to translate the probabilities. Test your algorithm on `state`, `n7_2A`, and `toulouse_neigh` with arbitrary $\beta$, $\alpha$, and $t$. Recovered vertices should appear in a different color (`colorant"purple"`).
    
###### The corrector should be able to write `new_state = SIR(net,state,beta,alpha,t)` with your code.

In [ ]:
"""
Take a contact network at a certain state and apply t time steps of an SIR model.

* PARAMS
    - net (LightGraph): graph representing the contact network
    - state (Array{Int32,1}): disease status of each vertex
    - beta (Float64): infection rate
    - alpha (Float64): curing rate
    - time (Int32): number of time step

* RETURNS
    - (Array{Int32,1}): The new state of the contact network after t time steps
"""
function SIR(net, state, beta, alpha, time)
    X = zeros(time+1, 3)
    adjacent_matrix = adjacency_matrix(net)
    n = nv(net)

    X[1, 1] = sum(state .== 0)
    X[1, 2] = sum(state .== 1)
    X[1, 3] = sum(state .== 2)

    for t = 2:(time+1)
        # println("-"^50, t)
        # println("state_0  = ", state)

        # on trouve le nombre de voisins de chaque individus
        adjacent_infected = adjacent_matrix * (state .== 1)
        # println("adjacent = ", number_infected_adjacent)

        # calcul des probas d'infection
        proba_infection = (state .== 0) .* (adjacent_infected .!= 0) .* (1 .- (
            (state .== 0) .* fill(1 - beta, n)
        ) .^ adjacent_infected)
        # println("proba_i  = ", proba_infection

        # tirage au sort des infections
        state[((state.==0).*(adjacent_infected.!=0).*rand(n)).<proba_infection] .= 1
        # println("state_i  = ", state)

        # tirage au sort des guérisons
        state[((state.==1).*rand(n)).>=(1-alpha)] .= 2
        # println("state_g  = ", state)

        X[t, 1] = sum(state .== 0)
        X[t, 2] = sum(state .== 1)
        X[t, 3] = sum(state .== 2)
    end
    return state, X
end

In [ ]:
# Test on Karat7
karat7_state = new_state(karat7, 1)
state, X = SIR(karat7, karat7_state, 0.7, 0.1, 10)

plot = Plots.plot(1:size(X)[1], X, labels=["Susceptible" "Infected" "Recovered"], palette=node_colors)
png("img/q10_1p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(karat7, nodefillc = nodefillc)
draw(PNG("img/q10_1g.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Test on n7_2A
n7_2A_state = new_state(n7_2A, 5)
state, X = SIR(n7_2A, n7_2A_state, 0.9, 0.1, 40)

plot = Plots.plot(1:size(X)[1], X, labels=["Susceptible" "Infected" "Recovered"], palette=node_colors)
png("img/q10_2p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(n7_2A, nodefillc = nodefillc)
draw(PNG("img/q10_2g.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Test on toulouse_neigh
toulouse_neigh_state = new_state(toulouse_neigh, 50)
state, X = SIR(toulouse_neigh, toulouse_neigh_state, 0.9, 0.1, 40)

plot = Plots.plot(1:size(X)[1], X, labels=["Susceptible" "Infected" "Recovered"], palette=node_colors)
png("img/q10_3p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(toulouse_neigh, nodefillc = nodefillc)
draw(PNG("img/q10_3g.png", 100cm, 100cm), plot)
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 11 (code):</strong> Implement the function `Simulation_SIR` (respect the header and the specifications).
    
###### The corrector should be able to write `predictions, taus = Simulation_SIR(net,nbinf,betas,alphas,t,nbsimu)` with your code.

In [ ]:
"""Take a contact network, different diseases (defined by different parameters alpha and beta), a number of initial infected people and process nbsimu simulations of SIR over t time steps. You will provide the prediction of the percentage of infected at each time t as well as the spreading rate of each disease.

* PARAMS
    - net (LightGraph): graph representing the contact network
    - nbinf (Int32): number of infected at the start of each simulation
    - betas (Array{Float64,1}): array of infection rate on edges
    - alphas (Array{Float64,1}): array of curing rate on vertices
    - t (Int32): number of time step
    - nbsimu (Int32): number of simulations

* RETURNS
    - (Array{Float64,3}): the prediction of the percentage of infected, the percentage of susceptible and the percentage of recovered at each time step and for each disease. The first dimension contains the time steps,the second contains the diseases, and the third the status(Infected: [:,:,1], Recovered: [:,:,2], Susceptible: [:,:,3])
    - (Array{Float64,1}): effective spreading rate for each disease
"""
function Simulation_SIR(net, nbinf, betas, alphas, t, nbsimu)
    taus = zeros(length(alphas))
    prediction = zeros(t+1, length(taus), 3)

    for (i, (beta, alpha)) in enumerate(zip(betas, alphas))
        taus[i] = round(beta / alpha, digits = 2)
        for _ in 1:nbsimu
            state = new_state(net, nbinf)
            _, X = SIR(net, state, beta, alpha, t)
            prediction[:, i, :] += X ./ nbsimu ./ length(state)
        end
    end

    return prediction, taus
end

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 12 (written):</strong> Run the script below and describe what you see. Why the infected curve does not behave the same as for SIS ? 
    
> TODO

In [ ]:
# Script launching prediction on one disease on n7_2A and plotting the percentage
# of infected, susceptible and recovered at each time step.
predictions, taus = Simulation_SIR(n7_2A, 2, [0.3], [0.2], 50, 1000)

plot = Plots.plot(
    [predictions[:, :, 1] predictions[:, :, 2] predictions[:, :, 3]],
    label = ["Infected" "Recovered" "Susceptible"],
    xlabel = "t",
    ylabel = "%",
    palette=node_colors
)
png("img/q12.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 13 (written):</strong> As for Question 6 script 2 plot the evolution of the percentage of infected for many $\tau$. Describe what you see.

> TODO

In [ ]:
# Equivalent experiment as for Question 6 script 2
# Script launching predictions on different diseases on karat7 and printing the precentage of infected at each time step.
betas = [0.05, 0.1, 0.01, 0.4, 0.04, 0.05, 0.005]
alphas = [0.05, 0.1, 0.01, 0.1, 0.01, 0.1, 0.01]

predictions, taus = Simulation_SIR(karat7, 2, betas, alphas, 100, 1000)
plot = Plots.plot(predictions[:, :, 2], label = taus', xlabel = "Time", ylabel = "% of infected")
png("img/q13_1.png")
display(plot)

In [ ]:
betas = [0.05, 0.1, 0.01, 0.4, 0.04, 0.05, 0.005]
alphas = [0.05, 0.1, 0.01, 0.1, 0.01, 0.1, 0.01]

predictions, taus = Simulation_SIR(n7_2A, 10, betas, alphas, 100, 1000)
plot = Plots.plot(predictions[:, :, 2], label = taus', xlabel = "Time", ylabel = "% of infected")
png("img/q13_2.png")
display(plot)

In [ ]:
# Same as before but applied on toulouse_neigh. May be a bit long to run.
betas = [0.05, 0.1, 0.15, 0.25, 0.35, 0.45, 0.55, 0.65, 0.75, 0.85, 0.95]
alphas = [0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2, 0.2]

predictions, taus = Simulation_SIR(toulouse_neigh, 100, betas, alphas, 100, 1000)
plot = Plots.plot(predictions[:, :, 2], label = taus', xlabel = "Time", ylabel = "% of infected")
png("img/q13_3.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cornflowerblue">Question 14 (code):</strong> Implement a script plotting the number of infected over 75 time steps for $\beta=0.3$ and $\alpha=0.2$ fixed and on 3 contact networks:
    
* A regular graph of 200 vertices with degree 2.
* A regular graph of 200 vertices with degree 5.
* A regular graph of 200 vertices with degree 10.

In [ ]:
# Plots of the number of infected people according to tau over 75 time steps for 3 contact networks.
n = 200
Plots.plot()
betas = [0.3]
alphas = [0.2]

plot = Plots.plot()
for d in [2 5 10]
    net = random_regular_graph(n, d)
    predictions, taus = Simulation_SIR(net, 1, betas, alphas, 75, 1000)
    Plots.plot!(predictions[:, :, 2], label = d, xlabel = "Time", ylabel = "% of infected")
end
Plots.plot!()

png("img/q14.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 15 (written):</strong> From the previous figure, explain why lockdown can be interesting when hospital places are lacking ?

> On observe qu'en diminuant le nombre de contacts potentiels entre les personnes d'un réseau, le nombre maximal d'infecté à un temps donné diminue. Ainsi par la mise en place d'un confinement les hopitaux peuvent être capable de supporter plus facilement la charge d'infectés.

<div style="width:75%;margin:0 auto;text-align:justify;">

### 2.2 SAIR
    
The vector containing the disease status `state` has to change a bit since we added a new state. Hence it will be an `Array{Int32,1}` where Susceptible=0, Infected=1, Recovered=2, and Alert=3.

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 16 (code):</strong> Implement the function `SAIR` (respect the header and the specifications). You can use `state` to translate the probabilities. Test your algorithm on `state`, `n7_2A`, and `toulouse_neigh` with arbitrary $\beta$, $\alpha$, and $t$. Alerted vertices should appear in a different color (`colorant"lightgreen"`).
    
###### The corrector should be able to write `new_state = SAIR(net,state,beta0,beta1,alpha,kappa,t)` with your code.

In [ ]:
"""Take a contact network at a certain state and apply t time steps of an SAIR model.

* PARAMS
    - net (LightGraph): graph representing the contact network
    - state (Array{Int32,1}): disease status of each vertex
    - beta0 (Float64): infection rate when not alert
    - beta1 (Float64): infection rate when alert
    - alpha (Float64): curing rate
    - kappa (Float64): alerting rate
    - t (Int32): number of time step

* RETURNS
    - (Array{Int32,1}): The new state of the contact network after t time steps
"""
function SAIR(net, state, beta0, beta1, alpha, kappa, time)
    X = zeros(time+1, 4)
    adjacent_matrix = adjacency_matrix(net)
    n = nv(net)

    X[1, 1] = sum(state .== 0)
    X[1, 2] = sum(state .== 1)
    X[1, 3] = sum(state .== 2)
    X[1, 4] = sum(state .== 3)

    for t = 2:(time+1)
        # println("-"^50, t)
        # println("state_0  = ", state)

        # on trouve le nombre de voisins de chaque individus
        adjacent_infected = adjacent_matrix * (state .== 1)
        # println("adjacent = ", number_infected_adjacent)

        # calcul des probas d'alert
        proba_alert = (state .== 0) .* (adjacent_infected .!= 0) .* (1 .- (
            (state .== 0) .* fill(1 - kappa, n)
        ) .^ adjacent_infected)
        # println("proba_a  = ", proba_alert)

        # tirage au sort les alerts
        state[((state.==0).*(adjacent_infected.!=0).*rand(n)).<proba_alert] .= 3
        # println("state_a  = ", state)

        # calcul des probas d'infection
        proba_infection = ((state .== 0) .+ (state .== 3)) .* (adjacent_infected .!= 0) .* (1 .- (
            (state .== 0) .* fill(1 - beta0, n)
            .+
            (state .== 3) .* fill(1 - beta1, n)
        ) .^ adjacent_infected)
        # println("proba_i  = ", proba_infection)

        # tirage au sort des infections
        state[(((state.==0).+(state.==3)).*(adjacent_infected.!=0).*rand(n)).<proba_infection] .= 1
        # println("state_i  = ", state)

        # tirage au sort des guérisons
        state[((state.==1).*rand(n)).>=(1-alpha)] .= 2
        # println("state_g  = ", state)

        X[t, 1] = sum(state .== 0)
        X[t, 2] = sum(state .== 1)
        X[t, 3] = sum(state .== 2)
        X[t, 4] = sum(state .== 3)
    end
    return state, X
end

In [ ]:
# Test on Karat7
karat7_state = new_state(karat7, 5)
state, X = SAIR(karat7, karat7_state, 0.9, 0.1, 0.1, 0.5, 10)

plot = Plots.plot(1:size(X)[1], X, label = ["Susceptible" "Infected" "Recovered" "Alert"], palette=node_colors)
png("img/q16_1p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(karat7, nodefillc = nodefillc)
draw(PNG("img/q16_1g.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Test on N7_2A
n7_2A_state = new_state(n7_2A, 10)
state, X = SAIR(n7_2A, n7_2A_state, 0.9, 0.05, 0.1, 0.5, 30)

plot = Plots.plot(1:size(X)[1], X, label = ["Infected" "Recovered" "Susceptible" "Alert"], palette=node_colors)
png("img/q16_2p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(n7_2A, nodefillc = nodefillc)
draw(PNG("img/q16_2g.png", 100cm, 100cm), plot)
display(plot)

In [ ]:
# Test on Toulouse_neigh
toulouse_neigh_state = new_state(toulouse_neigh, 50)
state, X = SAIR(toulouse_neigh, toulouse_neigh_state, 0.9, 0.1, 0.1, 0.5, 50)

plot = Plots.plot(1:size(X)[1], X, label = ["Infected" "Recovered" "Susceptible" "Alert"], palette=node_colors)
png("img/q16_3p.png")
display(plot)

nodefillc = node_colors[state.+1]
plot = gplot(toulouse_neigh, nodefillc = nodefillc)
draw(PNG("img/q16_3g.png", 100cm, 100cm), plot)
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 17 (code):</strong> Implement the function `Simulation_SAIR` (respect the header and the specifications).
    
###### The corrector should be able to write `predictions, taus = Simulation_SAIR(net,nbinf,betas0,betas1,alphas,kappas,t,nbsimu)` with your code.

In [ ]:
"""
Take a contact network, different diseases (defined by different parameters alpha and beta), a number of initial infected people and process nbsimu simulations of SAIR over t time steps. You will provide the prediction of the percentage of infected at each time t as well as the spreading rate of each disease.

* PARAMS
    - net (LightGraph): graph representing the contact network
    - nbinf (Int32): number of infected at the start of each simulation
    - betas0 (Array{Float64,1}): array of infection rate when not alert on edges
    - betas1 (Array{Float64,1}): array of infection rate when alert on edges
    - alphas (Array{Float64,1}): array of curing rate on vertices
    - kappas (Array{Float64,1}): array of alerting rate on edges
    - t (Int32): number of time step
    - nbsimu (Int32): number of simulations

* RETURNS
    - (Array{Float64,3}): the prediction of the percentage of infected, the percentage of susceptible and the percentage of recovered at each time step and for each disease. The first dimension contains the time steps, the second contains the diseases, and the third the status (Infected: [:,:,1], Recovered: [:,:,2], Susceptible: [:,:,3])
    - (Array{Float64,1}): effective spreading rate for each disease
"""
function Simulation_SAIR(net, nbinf, betas0, betas1, alphas, kappas, t, nbsimu)
    taus = zeros(length(alphas))
    prediction = zeros(t+1, length(taus), 4)

    for (i, (beta0, beta1, alpha, kappa)) in enumerate(zip(betas0, betas1, alphas, kappas))
        taus[i] = round(beta0 / alpha, digits = 2)
        for _ in 1:nbsimu
            state = new_state(net, nbinf)
            _, X = SAIR(net, state, beta0, beta1, alpha, kappa, t)
            prediction[:, i, :] += X ./ nbsimu ./ length(state)
        end
    end

    return prediction, taus
end

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 18 (written):</strong> Run the script below comparing the number of infected of SAIR and SIR and comment what you see.

> TODO

In [ ]:
# Script launching prediction on one disease on toulouse_neigh and plotting the percentage
# of infected at each time step for SIR and SAIR.
predictions1, _ = Simulation_SAIR(toulouse_neigh, 2, [0.2], [0.1], [0.1], [0.5], 100, 1000)
predictions2, _ = Simulation_SIR( toulouse_neigh, 2, [0.2], [0.1],               100, 1000)

plot = Plots.plot(
    [predictions1[:, :, 2] predictions2[:, :, 2]],
    label = ["SAIR" "SIR"],
    xlabel = "t",
    ylabel = "%"
)
png("img/q18.png")
display(plot)

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 19 (written):</strong> Of course the presented SIS, SIR, and SAIR models are limitated in their modelization of the reality. Formulate few of these limitations (at least 2). Propose few algorithm addons/ideas (at least 2) which would make the models more complex and more accurate in regards to the reality.
    
> TODO

<div style="width:75%;margin:0 auto;text-align:justify;">

## Part 3 - Discover patient zero
    
In the two previous parts you may have realised that understanding and controlling the spread of epidemics on contact networks is an important task. However, information about the origin of the epidemic could be also extremely useful to reduce or prevent future outbreaks. Thus, in this part we will focus on algorithm solutions to answer this issue.
    
The stochastic nature of infection propagation makes the estimation of the epidemic origin intrinsically hard: indeed, different initial conditions can lead to the same configuration at the observation time. Methods such as the distance centrality or the Jordan center try to approximate it. They both rely on spatial information by stating that the first infected is probably at the center of the cluster of infection. Mathematically:
    
* The jordan center is expressed as $\min_{v\in \mathcal{I}}\max_{n\in \mathcal{I}}d(v,n)$ where $\mathcal{I}$ is a connected component of the original contact network containing all infected and recovered vertices, and where $d(\cdot,\cdot)$ is the distance (= the shortest path) between 2 vertices (if not weighted graph each edge accounts for 1 unit). 
* The distance centrality is expressed as $\min_{v\in \mathcal{I}}\sum_{n\in \mathcal{I}}d(v,n)(\delta_{n,I} + \delta_{n,R}/\alpha)$, where $\delta_{n,I}=1$ if the vertex n is infected ($=0$ otherwise), and where $\delta_{n,R}=1$ if the vertex n is recovered ($=0$ otherwise). You may note that in distance centrality we increase the weight of the recovered vertices by a factor $1/\alpha$, it translates the fact that recovered vertices tend to be closer to the origin of the epidemic since they probably got ill before.
    
    
We formulate the problem as follow: given a contact network and a snapshot of epidemic spread at a certain time, determine the infection source. A snapshot is a given `state` array for a contact network.

###### A. Y. Lokhov, M. Mézard, H. Ohta, and L. Zdeborová, _"Inferring the origin of an epidemic with a dynamic message-passing algorithm"_, Physical Review (2014)

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 20 (code):</strong> Implement the function `jordan` (respect the header and the specifications). You will need to use the function `dijkstra_shortest_paths` of the LighGraphs library, refer to the doc for more information. If there are multiple minimal vertices, then return the first one.
    
###### The corrector should be able to write `zero = jordan(g,state,alpha)` with your code.

In [ ]:
function jordan(g, state)
    """Find patient zero by mean of the jordan center method.

    PARAMS
        g (LightGraph): graph representing the contact network
        state (Array{Int32,1}): disease status of each vertex

    RETURNS
        (Int32): the patient zero vertex number 
    """
    # TODO
end

<div style="width:75%;margin:0 auto;text-align:justify;">
    
<strong style="color:cornflowerblue">Question 21 (code):</strong> Implement the function `distance` (respect the header and the specifications). You will need to use the function `dijkstra_shortest_paths` of the LighGraphs library, refer to the doc for more information. If there are multiple minimal vertices, then return the first one.
    
###### The corrector should be able to write `zero = distance(g,state,alpha)` with your code.

In [ ]:
function distance(g, state, alpha = 1.0)
    """Find patient zero by mean of the distance centrality method.

    PARAMS
        g (LightGraph): graph representing the contact network
        state (Array{Int32,1}): disease status of each vertex
        alpha (Float64): curing rate

    RETURNS
        (Int32): the patient zero vertex number 
    """
    # TODO
end

<div style="width:75%;margin:0 auto;text-align:justify;">

<strong style="color:cadetblue">Question 22 (written):</strong> Run the 3 following scripts using your functions `state` and `state` and comment on the results.
    
The contact network is karat7 for 2 different patient zero and a $50\times 50$ grid. The real patient zero ("Z"), your jordan ("J") and distance ("D") approximations are appearing in `colorant"lightblue"`.

> TODO

In [ ]:
# Loading a snapshot of karat7
@load "karat7_Q22_1.jld2" g state pat_zero alpha beta loc_x loc_y

# Run the patient zero finding function
cent_pat_zero = distance(g, state, alpha)
jor_pat_zero = jordan(g, state)

# Some display options 
labels = Array{String,1}(undef, nv(g))
for k = 1:nv(g)
    if state[k] == 1
        labels[k] = "I"
    elseif state[k] == 2
        labels[k] = "R"
    else
        labels[k] = "S"
    end
end

if cent_pat_zero == jor_pat_zero == pat_zero
    labels[cent_pat_zero] = "C+J+Z"
elseif cent_pat_zero == jor_pat_zero
    labels[cent_pat_zero] = "C+J"
    labels[pat_zero] = "Z"
elseif cent_pat_zero == pat_zero
    labels[cent_pat_zero] = "C+Z"
    labels[jor_pat_zero] = "J"
elseif jor_pat_zero == pat_zero
    labels[jor_pat_zero] = "J+Z"
    labels[cent_pat_zero] = "C"
else
    labels[cent_pat_zero] = "C"
    labels[jor_pat_zero] = "J"
    labels[pat_zero] = "Z"
end

nodecolor = [colorant"lightseagreen", colorant"orange", colorant"purple"]
colors = nodecolor[state+ones(Int32, nv(g))]
colors[pat_zero] = colorant"lightblue"
colors[cent_pat_zero] = colorant"lightblue"
colors[jor_pat_zero] = colorant"lightblue"

# Display
draw(PNG("karat7_Q22_1.png", 20cm, 20cm), gplot(g, loc_x, loc_y, nodefillc = colors, nodelabel = labels))

In [ ]:
# Loading a snapshot of karat7
@load "karat7_Q22_2.jld2" g state pat_zero alpha beta loc_x loc_y

# Run the patient zero finding function
cent_pat_zero = distance(g, state, alpha)
jor_pat_zero = jordan(g, state)

# Some display options 
labels = Array{String,1}(undef, nv(g))
for k = 1:nv(g)
    if state[k] == 1
        labels[k] = "I"
    elseif state[k] == 2
        labels[k] = "R"
    else
        labels[k] = "S"
    end
end

if cent_pat_zero == jor_pat_zero == pat_zero
    labels[cent_pat_zero] = "C+J+Z"
elseif cent_pat_zero == jor_pat_zero
    labels[cent_pat_zero] = "C+J"
    labels[pat_zero] = "Z"
elseif cent_pat_zero == pat_zero
    labels[cent_pat_zero] = "C+Z"
    labels[jor_pat_zero] = "J"
elseif jor_pat_zero == pat_zero
    labels[jor_pat_zero] = "J+Z"
    labels[cent_pat_zero] = "C"
else
    labels[cent_pat_zero] = "C"
    labels[jor_pat_zero] = "J"
    labels[pat_zero] = "Z"
end

nodecolor = [colorant"lightseagreen", colorant"orange", colorant"purple"]
colors = nodecolor[state+ones(Int32, nv(g))]
colors[pat_zero] = colorant"lightblue"
colors[cent_pat_zero] = colorant"lightblue"
colors[jor_pat_zero] = colorant"lightblue"

# Display
draw(PNG("karat7_Q22_2.png", 20cm, 20cm), gplot(g, loc_x, loc_y, nodefillc = colors, nodelabel = labels))

In [ ]:
# Loading a snapshot of grid50
@load "grid50_Q22.jld2" g state pat_zero alpha beta loc_x loc_y

# Run the patient zero finding function
cent_pat_zero = distance(g, state, alpha)
jor_pat_zero = jordan(g, state)

# Some display options 
labels = Array{String,1}(undef, nv(g))
for k = 1:nv(g)
    if state[k] == 1
        labels[k] = "I"
    elseif state[k] == 2
        labels[k] = "R"
    else
        labels[k] = "S"
    end
end

if cent_pat_zero == jor_pat_zero == pat_zero
    labels[cent_pat_zero] = "C+J+Z"
elseif cent_pat_zero == jor_pat_zero
    labels[cent_pat_zero] = "C+J"
    labels[pat_zero] = "Z"
elseif cent_pat_zero == pat_zero
    labels[cent_pat_zero] = "C+Z"
    labels[jor_pat_zero] = "J"
elseif jor_pat_zero == pat_zero
    labels[jor_pat_zero] = "J+Z"
    labels[cent_pat_zero] = "C"
else
    labels[cent_pat_zero] = "C"
    labels[jor_pat_zero] = "J"
    labels[pat_zero] = "Z"
end

nodecolor = [colorant"lightseagreen", colorant"orange", colorant"purple"]
colors = nodecolor[state+ones(Int32, nv(g))]
colors[pat_zero] = colorant"lightblue"
colors[cent_pat_zero] = colorant"lightblue"
colors[jor_pat_zero] = colorant"lightblue"

# Display
draw(PNG("grid50_Q22.png", 100cm, 100cm), gplot(g, loc_x, loc_y, nodefillc = colors, nodelabel = labels))